In [35]:
from numpy import *

#My name: Joe Puccio
#Collaborators: Fred Landis, Alan Wu, Zen Yang

#Helper functions courtesy of Master McMillan
def GlobalAlign(v, w, match, mismatch, gap):
	s = zeros((len(v)+1,len(w)+1), dtype=int32)
	b = zeros((len(v)+1,len(w)+1), dtype=int32)

	for j in xrange(1,len(w)+1):
		s[0,j] = s[0,j-1] + gap
		b[0,j] = 1 

	for i in xrange(1,len(v)+1):
		s[i,0] = s[i-1,0] + gap
		b[i,0] = 2

	for i in xrange(1,len(v)+1):
		for j in xrange(1,len(w)+1):
			diag = s[i-1, j-1] + (match if (v[i-1] == w[j-1]) else mismatch)
			vskip = s[i-1, j] + gap
			wskip = s[i, j-1] + gap
			s[i,j] = max(vskip, wskip, diag)
			if (s[i,j] == wskip):
				b[i,j] = 1
			elif (s[i,j] == vskip):
				b[i,j] = 2
			else:
				b[i,j] = 3

	return s,b 
	#returns the score array and the backtrack array

def GlobalAlignForSubstring(v, w, match, mismatch, gap):
	s = zeros((len(v)+1,len(w)+1), dtype=int32)
	b = zeros((len(v)+1,len(w)+1), dtype=int32)

	#for j in xrange(1,len(w)+1):
	#	s[0,j] = s[0,j-1] + gap
	#	b[0,j] = 1 

	for i in xrange(1,len(v)+1):
		s[i,0] = s[i-1,0] + gap
		b[i,0] = 2

	for i in xrange(1,len(v)+1):
		for j in xrange(1,len(w)+1):
			diag = s[i-1, j-1] + (match if (v[i-1] == w[j-1]) else mismatch)
			vskip = s[i-1, j] + gap
			wskip = s[i, j-1] + gap
			s[i,j] = max(vskip, wskip, diag)
			if (s[i,j] == wskip):
				b[i,j] = 1
			elif (s[i,j] == vskip):
				b[i,j] = 2
			else:
				b[i,j] = 3

	return s,b 
	#returns the score array and the backtrack array

def alignWNonRecursive(b,w,i,j,local=False):
	while (b[i,j] != 0) and local:
		if (b[i,j] == 3):
			i = i-1
			j = j-1
		elif (b[i,j] == 2):
			i = i-1
		elif (b[i,j] == 1):
			j = j-1
	return j

In [32]:
#Problem 1

#It seems like this is just asking us to do Local Alignment between the fish and human sequence, and then the 
#difference from normal local alignment is that we're going to choose the alignment that starts in the first 
#colmun and ends in the last column (assuming human gene spans top row), because we need to make sure that the 
#resulting substring from the fish sequence actually has the start and end matching of the human sequence. 

with open("humanGene.seq", 'r') as sequenceFile:
	hGene = sequenceFile.read()
with open("mouseGene.seq", 'r') as sequenceFile:
	mGene = sequenceFile.read()
with open("yeastGene.seq", 'r') as sequenceFile:
	yGene = sequenceFile.read()
with open("zfishGene.seq", 'r') as sequenceFile:
	fGene = sequenceFile.read()

scores, backtrack = GlobalAlignForSubstring(hGene,fGene,1,0,-1)

In [36]:
print scores

[[    0     0     0 ...,     0     0     0]
 [   -1     0     0 ...,     1     1     1]
 [   -2    -1     1 ...,     1     1     1]
 ..., 
 [-2725 -2723 -2721 ...,  1609  1608  1607]
 [-2726 -2724 -2722 ...,  1611  1610  1609]
 [-2727 -2725 -2723 ...,  1613  1612  1611]]


In [16]:
print backtrack

[[0 0 0 ..., 0 0 0]
 [2 3 3 ..., 3 3 3]
 [2 2 3 ..., 3 3 3]
 ..., 
 [2 2 2 ..., 1 1 1]
 [2 2 2 ..., 1 1 1]
 [2 2 2 ..., 1 1 1]]


In [37]:
argmax(scores[len(hGene)]) 
#this gives us the end index we want for fish gene

3038

In [38]:
print alignWNonRecursive(backtrack,fGene,len(hGene),3038,True) 
#this gives us the start index we want for the fish gene

317


In [33]:
#So our start index of the fish gene is 317, and our end index is 3038. 

In [39]:
def get_all_substrings_return_dictionary_with_initial_count(string):
  length = len(string)
  adict = {}
  for i in xrange(length):
    for j in xrange(i,length):
      adict[string[i:j + 1]]=1 
  return adict

In [5]:
substringsOfYeast = get_all_substrings_return_dictionary_with_initial_count(yGene)
substringsOfHuman = get_all_substrings_return_dictionary_with_initial_count(hGene)
substringsOfMouse = get_all_substrings_return_dictionary_with_initial_count(mGene)
substringsOfFish = get_all_substrings_return_dictionary_with_initial_count(fGene)

#we save runtime if we only look at values that have been in all of them so far

substringsInYH = []
for substring in substringsOfYeast:
	if substring in substringsOfHuman: 
		substringsInYH.append(substring)
#print substringsInYH

substringsInYHM = []
for substring in substringsInYH:
	if substring in substringsOfMouse: 
		substringsInYHM.append(substring)
#print substringsInYHM

substringsInAll= []
for substring in substringsInYHM:
	if substring in substringsOfFish: 
		substringsInAll.append(substring)

print max(substringsInAll, key=len) 
#this prints the longest common substring in all of the gene sequences

AGAAGAGGA


In [34]:
#Problem 3

#Take the output of problem 1 in, because that's our last normalized sequence. 
fGene = fGene[317:3038]

score, back = GlobalAlign(yGene, hGene,1,0,-1)
print "Yeast and Human: ",score[len(yGene)][len(hGene)]

score, back = GlobalAlign(yGene, mGene,1,0,-1)
print "Yeast and Mouse: ",score[len(yGene)][len(mGene)]

score, back = GlobalAlign(yGene, fGene,1,0,-1)
print "Yeast and Fish: ",score[len(yGene)][len(fGene)]

score, back = GlobalAlign(fGene, hGene,1,0,-1)
print "Fish and Human: ",score[len(fGene)][len(hGene)]

score, back = GlobalAlign(fGene, mGene,1,0,-1)
print "Fish and Mouse: ",score[len(fGene)][len(mGene)]

score, back = GlobalAlign(mGene, hGene,1,0,-1)
print "Mouse and Human: ",score[len(mGene)][len(hGene)]

Yeast and Human:  320
Yeast and Mouse:  321
Yeast and Fish:  306
Fish and Human:  1723
Fish and Mouse:  1722
Mouse and Human:  2203
